# **\[SOLAR\]** SIMUL 1-ITERATION (INCREMENTAL)

JiyunLim  
2023-08-11

# SIMUL 1-ITERATION (INCREMENTAL)

여러조합으로 시뮬레이션 한 결과. (50에폭)

## Data

In [2]:
import pandas as pd
import numpy as np
import os

In [3]:
# read dataframe 
df = pd.read_csv('data_eng_230710.csv')

# make y, y_upper, y_period, time, regions 
y = df.loc[:,'Bukchoncheon':'Gyeongju-si'].to_numpy()
yU = df.loc[:,'Bukchoncheon_Upper':'Gyeongju-si_Upper'].to_numpy()
yP = np.divide(y, yU+1e-10)
t = df.loc[:,'date']
regions = list(df.loc[:,'Bukchoncheon':'Gyeongju-si'].columns)

TRAIN_RATIO = 0.8
T,N = len(t),len(regions) 
LEN_TEST = int(np.floor(T*(1-TRAIN_RATIO)))
LEN_TR = T - LEN_TEST

## GConvGRU

In [4]:
%run model/gconvgru

In [5]:
s1 = Simulator()

In [6]:
class GConv_GRU(torch.nn.Module):
    def __init__(self, node_features, filters):
        super(GConv_GRU, self).__init__()
        self.recurrent = GConvGRU(node_features, filters, 2)
        self.linear = torch.nn.Linear(filters, 1)

    def forward(self, x, edge_index, edge_weight):
        h = self.recurrent(x, edge_index, edge_weight)
        h = F.relu(h)
        h = self.linear(h)
        return h

In [ ]:
s1.simulate(
    n_iteration = 1,
    lags = [4, 8, 12],
    filters = [4, 8, 16, 32],
    epoch = [50],
    Model = GConv_GRU
)

method:classic lag:4 filters:4 epoch:50 is done
10/50

In [ ]:
fnames = ['./results/'+l for l in os.listdir('./results/') if l[0] != '.']
fnames 

## GConvLSTM / GCLSTM / LRGCN

In [ ]:
%run model/lstm

In [ ]:
s2 = Simulator()
s3 = Simulator()
s4 = Simulator()

In [ ]:
class GConv_LSTM(torch.nn.Module):
    def __init__(self, node_features, filters):
        super(GConv_LSTM, self).__init__()
        self.recurrent = GConvLSTM(in_channels = node_features, out_channels = filters, K = 2)
        self.linear = torch.nn.Linear(filters, 1)

    def forward(self, x, edge_index, edge_weight, h, c):
        h_0, c_0 = self.recurrent(x, edge_index, edge_weight, h, c)
        h = F.relu(h_0)
        h = self.linear(h)
        return h, h_0, c_0

In [ ]:
class GC_LSTM(torch.nn.Module):
    def __init__(self, node_features, filters):
        super(GC_LSTM, self).__init__()
        self.recurrent = GCLSTM(node_features, filters, 2)
        self.linear = torch.nn.Linear(filters, 1)

    def forward(self, x, edge_index, edge_weight, h, c):
        h_0, c_0 = self.recurrent(x, edge_index, edge_weight, h, c)
        h = F.relu(h_0)
        h = self.linear(h)
        return h, h_0, c_0

In [ ]:
class LR_GCN(torch.nn.Module):
    def __init__(self, node_features, filters):
        super(LR_GCN, self).__init__()
        self.recurrent = LRGCN(node_features, filters, 1, 1)
        self.linear = torch.nn.Linear(filters, 1)

    def forward(self, x, edge_index, edge_weight, h_0, c_0):
        h_0, c_0 = self.recurrent(x, edge_index, edge_weight, h_0, c_0)
        h = F.relu(h_0)
        h = self.linear(h)
        return h, h_0, c_0

In [ ]:
s2.simulate(
    n_iteration = 1,
    lags = [4, 8, 12],
    filters = [4, 8, 16, 32],
    epoch = [50],
    Model = GConv_LSTM
)


s3.simulate(
    n_iteration = 1,
    lags = [4, 8, 12],
    filters = [4, 8, 16, 32],
    epoch = [50],
    Model = GC_LSTM
)

s4.simulate(
    n_iteration = 1,
    lags = [4, 8, 12],
    filters = [4, 8, 16, 32],
    epoch = [50],
    Model = LR_GCN
)

In [ ]:
fnames = ['./results/'+l for l in os.listdir('./results/') if l[0] != '.']
fnames 

## TGCN

In [ ]:
%run model/tgcn

In [ ]:
s5 = Simulator()

In [ ]:
class T_GCN(torch.nn.Module):
    def __init__(self, node_features, filters):
        super(T_GCN, self).__init__()
        self.recurrent = TGCN(node_features, filters)
        self.linear = torch.nn.Linear(filters, 1)

    def forward(self, x, edge_index, edge_weight, prev_hidden_state):
        h = self.recurrent(x, edge_index, edge_weight, prev_hidden_state)
        y = F.relu(h)
        y = self.linear(y)
        return y, h

In [ ]:
s5.simulate(
    n_iteration = 1,
    lags = [4, 8, 12],
    filters = [4, 8, 16, 32],
    epoch = [50],
    Model = T_GCN
)

In [ ]:
fnames = ['./results/'+l for l in os.listdir('./results/') if l[0] != '.']
fnames 

## DCRNN

In [ ]:
%run model/dcrnn

In [ ]:
s6 = Simulator()

In [ ]:
class DC_RNN(torch.nn.Module):
    def __init__(self, node_features, filters):
        super(DC_RNN, self).__init__()
        self.recurrent = DCRNN(node_features, filters, 2)
        self.linear = torch.nn.Linear(filters, 1)

    def forward(self, x, edge_index, edge_weight):
        h = self.recurrent(x, edge_index, edge_weight)
        h = F.relu(h)
        h = self.linear(h)
        return h

In [ ]:
s6.simulate(
    n_iteration = 1,
    lags = [4, 8, 12],
    filters = [4, 8, 16, 32],
    epoch = [50],
    Model = DC_RNN
)

In [32]:
fnames = ['./results/'+l for l in os.listdir('./results/') if l[0] != '.']
fnames 

In [33]:
df1 = pd.read_csv('./results/SOLAR_2023-08-10 16:21:53.644069_gconvgru.csv')
df2 = pd.read_csv('./results/SOLAR_2023-08-09 14:49:05.496417_gconvlstm.csv')
df3 = pd.read_csv('./results/SOLAR_2023-08-09 22:28:42.656389_gclstm.csv')
df4 = pd.read_csv('./results/SOLAR_2023-08-10 06:11:00.623632_lrgcn.csv')
df5 = pd.read_csv('./results/SOLAR_2023-08-10 12:22:28.191936_tgcn.csv')
df6 = pd.read_csv('./results/SOLAR_2023-08-10 20:52:50.851556_dcrnn.csv')

## RSLT

In [36]:
# df_ = pd.concat([pd.read_csv(fname) for fname in fnames]).reset_index(drop=True)

In [99]:
df_ = pd.concat([df1, df2, df3, df4, df5, df6])
df_.head(2)

In [86]:
# pd.set_option('display.max_rows', None)

In [88]:
df_summary = df_.groupby(by=['model','method','lags','nof_filters']).agg({'mse':[np.mean, np.std]}).reset_index()
df_summary

## `*` GConvGRU

In [89]:
model_name_lst = df_summary['model'].unique()
model_name_lst 

In [90]:
def model_rslt(df, model_name):
    return df[df['model']==model_name]

def compare_method(df, model_name):
    model_rslt_ = model_rslt(df, model_name)
    model_rslt_c = model_rslt_[model_rslt_['method']=='classic'].reset_index(drop=True)
    model_rslt_p = model_rslt_[model_rslt_['method']=='proposed'].reset_index(drop=True)[['method','mse']]
    rslt_ = pd.concat([model_rslt_c, model_rslt_p] ,axis=1)
    return rslt_

In [91]:
compare_method(df_summary, 'GConvGRU')

## `*` GConvLSTM

In [92]:
compare_method(df_summary, 'GConvLSTM')

-   lag=12, filter=8

## `*` GCLSTM

In [93]:
compare_method(df_summary, 'GCLSTM')

-   lag=12, filter=16

## `*` LRGCN

In [94]:
compare_method(df_summary, 'LRGCN')

## `*` TGCN

In [95]:
compare_method(df_summary, 'TGCN')

## `*` DCRNN

In [96]:
compare_method(df_summary, 'DCRNN')

-   TGCN, LRGCN?

## LRGCN 100 epoch

In [102]:
%run model/lstm

In [103]:
s4_100 = Simulator()

In [ ]:
# LR-GCN
s4_100.simulate(
    n_iteration = 1,
    lags = [4, 8],
    filters = [4, 8, 16],
    epoch = [100],
    Model = LR_GCN
)

method:classic lag:4 filters:4 epoch:100 is done
method:classic lag:4 filters:8 epoch:100 is done
method:classic lag:4 filters:16 epoch:100 is done
method:classic lag:8 filters:4 epoch:100 is done
method:classic lag:8 filters:8 epoch:100 is done
method:classic lag:8 filters:16 epoch:100 is done
method:proposed lag:4 filters:4 epoch:100 is done
method:proposed lag:4 filters:8 epoch:100 is done
method:proposed lag:4 filters:16 epoch:100 is done
69/100

In [ ]:
# fnames = ['./results/'+l for l in os.listdir('./results/') if l[0] != '.']
# fnames 

In [109]:
lrgcn_100 = pd.read_csv('./results/test/SOLAR_2023-08-11 08:50:35.146661_lrgcn.csv')

In [112]:
lrgcn_100_summary = df_.groupby(by=['model','method','lags','nof_filters']).agg({'mse':[np.mean, np.std]}).reset_index()
compare_method(lrgcn_100_summary, 'LRGCN')

## TGCN 100 epoch

In [113]:
%run model/tgcn

In [114]:
s5_100 = Simulator()

In [ ]:
# TGCN
s5_100.simulate(
    n_iteration = 1,
    lags = [4, 8],
    filters = [4, 8, 16],
    epoch = [100],
    Model = T_GCN
)

method:classic lag:4 filters:4 epoch:100 is done
method:classic lag:4 filters:8 epoch:100 is done
method:classic lag:4 filters:16 epoch:100 is done
method:classic lag:8 filters:4 epoch:100 is done
method:classic lag:8 filters:8 epoch:100 is done
method:classic lag:8 filters:16 epoch:100 is done
method:proposed lag:4 filters:4 epoch:100 is done
method:proposed lag:4 filters:8 epoch:100 is done
method:proposed lag:4 filters:16 epoch:100 is done
method:proposed lag:8 filters:4 epoch:100 is done
12/100